In [1]:
import numpy as np
import pandas as pd
import math
import sys
from ipynb.fs.full.Formulas import *

Lassi


In [2]:
class Vehicle:
    def __init__(self, x, y, velocity):
        self.x = x
        self.y = y
        self.velocity = velocity
        
    def calculate_position(self,time):
        current_x=self.x+(self.velocity*time)
        return current_x, self.y

class UAV:
    def __init__(self,x,y,height,velocity,theta,radius=500):
        self.x = x
        self.y = y
        self.height = height
        self.radius = radius
        self.velocity = velocity
        self.theta = theta

    def calculate_cords(self,time):
        angle = (self.velocity*time)%(2*math.pi)
        current_x=self.x+(self.radius*math.cos(angle))
        current_y=self.y+(self.radius*math.sin(angle))
        return current_x,current_y 


In [3]:
class Relay:    

    def isbetween(self,middle,x,y):
        left=min(x,y)
        right=max(x,y)
        return middle > left and middle < right
        
    def no_of_obstacles(self,vehicle1,vehicle2,time):
        vehicle1_x,vehicle1_y=vehicle1.calculate_position(time)
        vehicle2_x,vehicle2_y=vehicle2.calculate_position(time)
        ans=0
        for vehicle in list_of_vehicles:
            current_x,current_y=vehicle.calculate_position(time)
            if current_y == vehicle1_y and self.isbetween(current_x,vehicle1_x,vehicle2_x):
                ans+=1
        return ans    
    
    def determine_relay_type(self,vehicle1,vehicle2,time):
        vehicle1_x,vehicle1_y=vehicle1.calculate_position(time)
        vehicle2_x,vehicle2_y=vehicle2.calculate_position(time)
        
        if vehicle1_y == vehicle2_y:    #Sender and Receiver on same lane
            obstacles = self.no_of_obstacles(vehicle1,vehicle2,time)
            if obstacles == 0:
                return 'dont_relay', set()
            elif obstacles == 1:
                return 'same_lane_relay', self.candidate_relay_set_single_same_lane(vehicle1,vehicle2,time) 
            else:
                return 'adjacent_lane_relay', self.candidate_relay_set_multiple_same_lane(vehicle1,vehicle2,time)
        elif abs(vehicle1_y - vehicle2_y) == 1: # Sender and Receiver on adjacent lanes
            return 'dont_relay', set()
        else:     # Sender and Receiver 
            return 'middle_lane_relay', self.candidate_relay_set_middle_lane(vehicle1,vehicle2,time)

    # Vehicle 1 =sender and Vehicle 2=receiver
    
    def candidate_relay_set_middle_lane(self,vehicle1,vehicle2,time):
        candidate_relays=set()
        vehicle1_x_start,vehicle1_y_start=vehicle1.calculate_position(time)
        vehicle2_x_start,vehicle2_y_start=vehicle2.calculate_position(time)

        if vehicle1_y_start > vehicle2_y_start:
            return self.candidate_relay_set_middle_lane(vehicle2,vehicle1,time)
        
        vehicle1_x_end,vehicle1_y_end=vehicle1.calculate_position(time+slot_duration)
        vehicle2_x_end,vehicle2_y_end=vehicle2.calculate_position(time+slot_duration)
        
        for vehicle in list_of_vehicles:
            current_x_start,current_y_start=vehicle.calculate_position(time)
            current_x_end,current_y_end=vehicle.calculate_position(time+slot_duration)
            if self.isbetween(current_y_start,vehicle1_y_start,vehicle2_y_start)==0: 
                continue

            m = current_y_start - vehicle1_y_start
            n = vehicle2_y_start - current_y_start
            D1x , D1y = section_formula(vehicle1_x_start,vehicle1_y_start,vehicle2_x_start,vehicle2_y_start,m,n)
            D2x , D2y = section_formula(vehicle1_x_end,vehicle1_y_end,vehicle2_x_end,vehicle2_y_end,m,n)
            
            if current_x_end <= D1x or D2x <= current_x_start: # No overlap=No add
                continue

            start_boundary=max(current_x_start,D1x)
            end_boundary = min(current_x_end, D2x)
            epsilon = (end_boundary-start_boundary) / (current_x_end - current_x_start) 
            if epsilon >= 0.5:
                candidate_relays.add(vehicle)        
            
        # If candidate_relays.length()==0 till now, it means there's no obstacle in middle lanes and no need to relay. so dont add uav and return empty set
        if len(candidate_relays):
            candidate_relays=candidate_relays.union(self.get_uav(vehicle1,vehicle2,time))
        return candidate_relays

    def candidate_relay_set_single_same_lane(self,vehicle1,vehicle2,time):
        candidate_relays=set()
        vehicle1_x,vehicle1_y=vehicle1.calculate_position(time)
        vehicle2_x,vehicle2_y=vehicle2.calculate_position(time)
        for vehicle in list_of_vehicles:
            current_x,current_y=vehicle.calculate_position(time)
            if self.isbetween(current_x,vehicle1_x,vehicle2_x):
                candidate_relays.add(vehicle)
                break
        candidate_relays=candidate_relays.union(self.get_uav(vehicle1,vehicle2,time))
        return candidate_relays

    def candidate_relay_set_multiple_same_lane(self,vehicle1,vehicle2,time):
        candidate_relays=set()
        vehicle1_x_start,vehicle1_y_start=vehicle1.calculate_position(time)
        vehicle2_x_end,vehicle2_y_end=vehicle2.calculate_position(time+slot_duration)
        D3x=vehicle1_x_start
        D4x=vehicle2_x_end
        
        for vehicle in list_of_vehicles:
            current_x_start,current_y_start=vehicle.calculate_position(time)
            current_x_end,current_y_end=vehicle.calculate_position(time+slot_duration)
            
            if current_y_start==(vehicle1_y_start-1) or current_y_start==(vehicle1_y_start+1):
                if current_x_end <= D3x or D4x <= current_x_start:
                    continue
                
                start_boundary=max(current_x_start, D3x)
                end_boundary=min(current_x_end, D4x)
                epsilon=(end_boundary-start_boundary)/(current_x_end-current_x_start)
                
                if epsilon>=0.5:
                    candidate_relays.add(vehicle)
                    
        candidate_relays=candidate_relays.union(self.get_uav(vehicle1,vehicle2,time))
        return candidate_relays

    def get_uav(self,vehicle1,vehicle2,time):
        candidate_uavs=set()
        vehicle1_x,vehicle1_y=vehicle1.calculate_position(time)
        vehicle2_x,vehicle2_y=vehicle2.calculate_position(time)
        for uav in candidate_uavs:
            current_x,current_y=uav.calculate_cords(time)
            distance_s = ((current_x-vehicle1_x)**2) + ((current_y-vehicle1_y)**2)
            distance_s = math.sqrt(distance_s)
            distance_r = ((current_x-vehicle2_x)**2) + ((current_y-vehicle2_y)**2)
            distance_r = math.sqrt(distance_r)
            if distance_s <= 500 and distance_r <= 500:
                candidate_uavs.add(uav)
        return candidate_uavs
        

In [4]:
# Declare it in more proper manner
list_of_vehicles = [
        Vehicle(10, 1, 75),    
        Vehicle(15, 2, 70),    
        Vehicle(20, 3, 65),    
        Vehicle(25, 1, 60),    
        Vehicle(30, 2, 55),    
        Vehicle(35, 3, 50),    
        Vehicle(40, 1, 45),    
        Vehicle(45, 2, 40),    
        Vehicle(50, 3, 35),    
        Vehicle(55, 1, 30)     
]

# Creating a list of UAV objects
list_of_uavs = [
        UAV(10, 1, 200, 4, math.pi/4),
        UAV(500, 2, 150, 10, math.pi/3),
        UAV(200, 3, 250, 7, math.pi/6)
]

# Create an empty list to store flows
flows = []

# Loop through the list and form pairs
for i in range(len(list_of_vehicles)):
    for j in range(i+1, len(list_of_vehicles)):  # Ensure unique pairs
        flows.append([list_of_vehicles[i], list_of_vehicles[j]])

# Convert the list of pairs to a NumPy array
flows = np.array(flows)

# Print the 2D NumPy array
# for i in flows:
#     for j in i:
#         x= str(j.x) + " " + str(j.y)
#         print(x)

# Edging

In [5]:
# nahi kari 6 ghante leetcode. Isliye idhar testing karni pad rahi hai

# Open a file in write mode
with open('output.txt', 'w') as f:
    # Redirect stdout to the file
    sys.stdout = f
    
    # Your print statements
    temp= Relay()
    for i in range(5):
        time = i*slot_duration
        for j in flows:
            print("Sender:",j[0].calculate_position(time),"Receiver:",j[1].calculate_position(time))
            relay_type,candidate_set=temp.determine_relay_type(j[0],j[1],time)
            for k in candidate_set:
                print(k.calculate_position(time))
            # print(temp.determine_relay_type(j[0],j[1],i*slot_duration))
    
    # Remember to restore stdout to its default value after writing
    sys.stdout = sys.__stdout__

# File is automatically closed after the `with` block

[(10.0, 1), (15.0, 2), 0.0]
[(10.0, 1), (20.0, 3), 0.0]
[(10.0, 1), (25.0, 1), 0.0]
[(10.0, 1), (30.0, 2), 0.0]
[(10.0, 1), (35.0, 3), 0.0]
[(10.0, 1), (40.0, 1), 0.0]
[(10.0, 1), (45.0, 2), 0.0]
[(10.0, 1), (50.0, 3), 0.0]
[(10.0, 1), (55.0, 1), 0.0]
[(15.0, 2), (20.0, 3), 0.0]
[(15.0, 2), (25.0, 1), 0.0]
[(15.0, 2), (30.0, 2), 0.0]
[(15.0, 2), (35.0, 3), 0.0]
[(15.0, 2), (40.0, 1), 0.0]
[(15.0, 2), (45.0, 2), 0.0]
[(15.0, 2), (50.0, 3), 0.0]
[(15.0, 2), (55.0, 1), 0.0]
[(20.0, 3), (25.0, 1), 0.0]
[(20.0, 3), (30.0, 2), 0.0]
[(20.0, 3), (35.0, 3), 0.0]
[(20.0, 3), (40.0, 1), 0.0]
[(20.0, 3), (45.0, 2), 0.0]
[(20.0, 3), (50.0, 3), 0.0]
[(20.0, 3), (55.0, 1), 0.0]
[(25.0, 1), (30.0, 2), 0.0]
[(25.0, 1), (35.0, 3), 0.0]
[(25.0, 1), (40.0, 1), 0.0]
[(25.0, 1), (45.0, 2), 0.0]
[(25.0, 1), (50.0, 3), 0.0]
[(25.0, 1), (55.0, 1), 0.0]
[(30.0, 2), (35.0, 3), 0.0]
[(30.0, 2), (40.0, 1), 0.0]
[(30.0, 2), (45.0, 2), 0.0]
[(30.0, 2), (50.0, 3), 0.0]
[(30.0, 2), (55.0, 1), 0.0]
[(35.0, 3), (40.0, 1

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



 (10782.5, 2), 195.5]
[(11755.0, 1), (9810.0, 3), 195.5]
[(11755.0, 1), (8837.5, 1), 195.5]
[(11755.0, 1), (7865.0, 2), 195.5]
[(11755.0, 1), (6892.5, 3), 195.5]
[(11755.0, 1), (5920.0, 1), 195.5]
[(10782.5, 2), (9810.0, 3), 195.5]
[(10782.5, 2), (8837.5, 1), 195.5]
[(10782.5, 2), (7865.0, 2), 195.5]
[(10782.5, 2), (6892.5, 3), 195.5]
[(10782.5, 2), (5920.0, 1), 195.5]
[(9810.0, 3), (8837.5, 1), 195.5]
[(9810.0, 3), (7865.0, 2), 195.5]
[(9810.0, 3), (6892.5, 3), 195.5]
[(9810.0, 3), (5920.0, 1), 195.5]
[(8837.5, 1), (7865.0, 2), 195.5]
[(8837.5, 1), (6892.5, 3), 195.5]
[(8837.5, 1), (5920.0, 1), 195.5]
[(7865.0, 2), (6892.5, 3), 195.5]
[(7865.0, 2), (5920.0, 1), 195.5]
[(6892.5, 3), (5920.0, 1), 195.5]
[(14680.000000000002, 1), (13707.000000000002, 2), 195.60000000000002]
[(14680.000000000002, 1), (12734.000000000002, 3), 195.60000000000002]
[(14680.000000000002, 1), (11761.000000000002, 1), 195.60000000000002]
[(14680.000000000002, 1), (10788.000000000002, 2), 195.60000000000002]
[(14

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



 185.0]
[(12045.0, 3), (6525.0, 3), 185.0]
[(12045.0, 3), (5605.0, 1), 185.0]
[(11125.0, 1), (10205.0, 2), 185.0]
[(11125.0, 1), (9285.0, 3), 185.0]
[(11125.0, 1), (8365.0, 1), 185.0]
[(11125.0, 1), (7445.0, 2), 185.0]
[(11125.0, 1), (6525.0, 3), 185.0]
[(11125.0, 1), (5605.0, 1), 185.0]
[(10205.0, 2), (9285.0, 3), 185.0]
[(10205.0, 2), (8365.0, 1), 185.0]
[(10205.0, 2), (7445.0, 2), 185.0]
[(10205.0, 2), (6525.0, 3), 185.0]
[(10205.0, 2), (5605.0, 1), 185.0]
[(9285.0, 3), (8365.0, 1), 185.0]
[(9285.0, 3), (7445.0, 2), 185.0]
[(9285.0, 3), (6525.0, 3), 185.0]
[(9285.0, 3), (5605.0, 1), 185.0]
[(8365.0, 1), (7445.0, 2), 185.0]
[(8365.0, 1), (6525.0, 3), 185.0]
[(8365.0, 1), (5605.0, 1), 185.0]
[(7445.0, 2), (6525.0, 3), 185.0]
[(7445.0, 2), (5605.0, 1), 185.0]
[(6525.0, 3), (5605.0, 1), 185.0]
[(13892.500000000002, 1), (12972.000000000002, 2), 185.10000000000002]
[(13892.500000000002, 1), (12051.500000000002, 3), 185.10000000000002]
[(13892.500000000002, 1), (11131.000000000002, 1), 185

![GURU](guru.webp) 

# Creating flows and storing their candidate sets

In [8]:
flows_candidate_relay_set_pairs={}
RelayObj = Relay()
for current_time_slot in range(number_of_time_slots):
    time = current_time_slot * slot_duration
    for flow in flows:
        flow_with_time = [flow[0].calculate_position(time), flow[1].calculate_position(time), time]
        flow_with_time = str(flow_with_time)
        # print(flow_with_time)
        relay_type,candidate_set = RelayObj.determine_relay_type(flow[0],flow[1],time)
        flows_candidate_relay_set_pairs[flow_with_time] = [relay_type,candidate_set]

# Algo 1